In [38]:
import pandas as pd
from torch import nn
import torch
from torch.utils.data import DataLoader
import torch.optim as optim
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import StandardScaler


In [39]:
data = pd.read_csv('data.csv')
data.head()

rarity  size   color          species    country
0    Common   4.5   Green         TreeFrog        USA
1  Uncommon   3.2   Brown         Bullfrog     Canada
2    Common   5.1    Blue         TreeFrog     Mexico
3      Rare   6.7     Red  RedEyedTreeFrog     Brazil
4    Common   2.8  Yellow       BananaFrog  Australia

In [40]:

# Preprocess data
label_encoder = LabelEncoder()
data['species'] = label_encoder.fit_transform(data['species'])
data['rarity'] = label_encoder.fit_transform(data['rarity'])  # Encode the 'rarity' column
data['color'] = label_encoder.fit_transform(data['color'])
data['country'] = label_encoder.fit_transform(data['country'])


X = data.drop(['species'], axis=1).values
y = data['species'].values

# Split data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)



In [41]:
X_train_tensor = torch.tensor(X_train, dtype=torch.float32)
y_train_tensor = torch.tensor(y_train, dtype=torch.int64)
X_test_tensor = torch.tensor(X_test, dtype=torch.float32)
y_test_tensor = torch.tensor(y_test, dtype=torch.int64)

In [42]:
# deep nn

class SimpleNN(nn.Module):
    def __init__(self,input_size,hidden_size,output_size):
        super(SimpleNN,self).__init__()
        self.fc1 = nn.Linear(input_size,hidden_size)
        self.relu = nn.ReLU()
        self.fc2 = nn.Linear(hidden_size,output_size)

    def forward(self,x):
        x = self.relu(self.fc1(x))
        x = self.fc2(x)
        return x


In [50]:
input_size = 4
hidden_size = 64 
output_size = len(label_encoder.classes_)

model = SimpleNN(input_size=input_size,hidden_size=hidden_size,output_size=output_size)
optimizer = optim.Adam(model.parameters(),lr=0.001)
loss_fn = nn.CrossEntropyLoss()

output_size



5

In [47]:
num_epochs = 10
batch_size = 32

for epoch in range(num_epochs):
    for i in range(0, len(X_train_tensor), batch_size):
        inputs = X_train_tensor[i:i + batch_size]
        labels = y_train_tensor[i:i + batch_size]

        optimizer.zero_grad()
        outputs = model(inputs)
        loss = loss_fn(outputs, labels)
        loss.backward()
        optimizer.step()

    print(f'Epoch [{epoch + 1}/{num_epochs}], Loss: {loss.item():.4f}')


Epoch [1/10], Loss: 1.5100
Epoch [2/10], Loss: 1.4834
Epoch [3/10], Loss: 1.4557
Epoch [4/10], Loss: 1.4273
Epoch [5/10], Loss: 1.3985
Epoch [6/10], Loss: 1.3693
Epoch [7/10], Loss: 1.3398
Epoch [8/10], Loss: 1.3105
Epoch [9/10], Loss: 1.2812
Epoch [10/10], Loss: 1.2522


In [49]:
# Save the model
torch.save(model.state_dict(), 'your_model.pth')


In [51]:
loaded_model = SimpleNN(input_size=input_size, hidden_size=hidden_size, output_size=output_size)

In [52]:
loaded_model.load_state_dict(torch.load('your_model.pth'))

<All keys matched successfully>

In [53]:
loaded_model.eval()

SimpleNN(
  (fc1): Linear(in_features=4, out_features=64, bias=True)
  (relu): ReLU()
  (fc2): Linear(in_features=64, out_features=5, bias=True)
)

In [55]:
with torch.no_grad():
    # Make predictions on the test set
    loaded_outputs = loaded_model(X_test_tensor)

    # Convert the model outputs to class predictions
    _, predicted_labels = torch.max(loaded_outputs, 1)

    # Evaluate accuracy
    accuracy = (predicted_labels == y_test_tensor).sum().item() / len(y_test_tensor)
    print(f'Test Accuracy: {accuracy * 100:.2f}%')

Test Accuracy: 80.00%
